In [1]:
from rdkit import Chem
from rdkit.Chem import AllChem
import numpy as np

# --- 1) 基準フラグメントを用意（SMILES or MolBlock） ---
# ここでは例としてフタル酸のSMILES（実際は正確なSMILESに置き換えてください）
phthalic_smiles = "O=C(O)C1=CC=CC=C1C(=O)O"  # 例（フタル酸類似）
frag = Chem.AddHs(Chem.MolFromSmiles(phthalic_smiles))
AllChem.EmbedMolecule(frag, randomSeed=0)
AllChem.MMFFOptimizeMolecule(frag)


# 基準フラグメントの座標配列
frag_conf = frag.GetConformer()
frag_coords = np.array([frag_conf.GetAtomPosition(i) for i in range(frag.GetNumAtoms())])

# for atom in frag.GetAtoms():
    # pos = frag_conf.GetAtomPosition(atom.GetIdx())
    # print(f"{atom.GetSymbol()} {pos.x:.4f} {pos.y:.4f} {pos.z:.4f}")

# --- 2) 置換体リスト（SMILESの例） ---
smiles_list = [
    "O=C(O)C=1C=C(C(=O)O)C(=CC1C(=O)O)C(=O)O",  # 置換例
]

def prepare_and_fix(smiles, frag_template, frag_coords):
    mol = Chem.AddHs(Chem.MolFromSmiles(smiles))
    AllChem.EmbedMolecule(mol, randomSeed=0)
    AllChem.MMFFOptimizeMolecule(mol)

    # 部分構造一致（フラグメントの重心などでマッチする想定）
    match = mol.GetSubstructMatch(Chem.RemoveHs(frag_template))  # frag_templateはH付きでも可
    if not match:
        raise ValueError("フラグメントが見つかりません: " + smiles)

    # match は mol 中の該当原子インデックスのタプル（順序はフラグメントの原子順に対応）
    conf = mol.GetConformer()
    # 位置を基準フラグメントの座標に上書き
    for i_frag, atom_idx in enumerate(match):
        x, y, z = frag_coords[i_frag]
        conf.SetAtomPosition(atom_idx, (float(x), float(y), float(z)))

    # 固定する原子インデックス（上書きしたフラグメント部分）
    fixed_atoms = list(match)

    # 置換部のみを最適化（フラグメントは固定）
    # RDKitのUFF最適化に fixedAtoms 引数を使う
    try:
        AllChem.UFFOptimizeMolecule(mol, maxIters=200, fixedAtoms=fixed_atoms)
    except Exception:
        # 失敗しても座標は書き出す選択肢あり
        pass

    return mol

print(frag_coords)

[[ 2.97442392 -0.82837423 -0.2808328 ]
 [ 1.9929179  -0.18386229 -0.59537218]
 [ 2.04531068  0.83784675 -1.46645921]
 [ 0.60422138 -0.4818327  -0.21111594]
 [ 0.17990648 -1.81289236 -0.33786572]
 [-1.14023185 -2.15785768 -0.04558074]
 [-2.0383432  -1.1792838   0.3778421 ]
 [-1.61450906  0.14378784  0.52553698]
 [-0.28643949  0.49950833  0.23906003]
 [ 0.16963125  1.88099744  0.50255923]
 [ 1.26432343  2.22130444  0.90683701]
 [-0.80017679  2.78041405  0.25442478]
 [ 3.00346281  0.96255529 -1.63102295]
 [ 0.87600781 -2.57888066 -0.67524673]
 [-1.4684662  -3.18957903 -0.15100276]
 [-3.06762337 -1.44804512  0.60553514]
 [-2.32051472  0.89113695  0.88210995]
 [-0.37390101  3.64305678  0.44249885]]


In [2]:
for i, smi in enumerate(smiles_list):
    try:
        mol = prepare_and_fix(smi, frag, frag_coords)
    except Exception as e:
        print("処理失敗:", smi, e)
        continue

    conf = mol.GetConformer()
    for atom in mol.GetAtoms():
        pos = conf.GetAtomPosition(atom.GetIdx())
        print(f"{atom.GetSymbol()} {pos.x:.4f} {pos.y:.4f} {pos.z:.4f}")

O 2.9744 -0.8284 -0.2808
C 1.9929 -0.1839 -0.5954
O 2.0453 0.8378 -1.4665
C 0.6042 -0.4818 -0.2111
C 0.1799 -1.8129 -0.3379
C -1.1402 -2.1579 -0.0456
C 2.4914 1.0404 -0.8262
O 3.3674 0.4646 -1.4398
O 2.5761 2.3467 -0.5201
C -2.0383 -1.1793 0.3778
C -1.6145 0.1438 0.5255
C -0.2864 0.4995 0.2391
C 0.1696 1.8810 0.5026
O 1.2643 2.2213 0.9068
O -0.8002 2.7804 0.2544
C 2.3663 -1.7226 0.2302
O 2.4716 -2.8688 -0.1580
O 3.3078 -1.1073 0.9628
H -3.2288 2.9002 -0.8334
H 0.0912 2.2591 -0.6968
H 3.4516 2.6195 -0.8692
H -0.1007 -2.4942 0.7693
H -4.1951 -1.6849 0.0787
H 4.0568 -1.7406 0.9779


In [3]:
import pandas as pd
import numpy as np


df = pd.read_csv("sample/basis.txt", sep="\\s+" ,names=["atom", "x", "y", "z"])
coordinates = df[["x","y","z"]].to_numpy()
print(coordinates)
coordinates[0]+coordinates[1]

[[ 0.873705  0.107504 -0.415645]
 [-0.047389  1.086085 -0.023398]
 [ 0.409205  2.346917  0.339506]
 [ 1.767517  2.632594  0.331346]
 [ 2.679469  1.656416 -0.040223]
 [ 2.23294   0.396172 -0.412647]
 [ 0.470232 -1.235815 -0.910904]
 [-1.509717  0.820389  0.104293]
 [-1.78471  -0.364806  0.616804]
 [-2.358431  1.640615 -0.191208]
 [ 1.006335 -2.271573 -0.571851]
 [-0.49816  -1.194838 -1.820764]
 [-0.30539   3.09753   0.652258]
 [ 2.111111  3.617014  0.623709]
 [ 3.740227  1.87375  -0.046519]
 [ 2.93764  -0.363819 -0.725624]
 [-2.77601  -0.520723  0.661077]
 [-0.722202 -2.100159 -2.095972]
 [-4.352326 -0.894566  0.79883 ]
 [-4.606586 -1.61514   0.208294]
 [-4.892529 -0.14124   0.527397]
 [ 2.810453 -2.537663  1.596857]
 [ 2.474792 -3.297862  2.084137]
 [ 2.197885 -2.428282  0.847922]]


array([ 0.826316,  1.193589, -0.439043])

In [4]:
a = (1,2,3,4)
a = list(a)
a.append(5)

In [5]:
import numpy as np

def rotation_matrix(axis, theta):
    axis = np.array(axis, float)
    axis /= np.linalg.norm(axis)
    x, y, z = axis
    c, s = np.cos(theta), np.sin(theta)
    C = 1 - c
    return np.array([
        [c + x*x*C,     x*y*C - z*s, x*z*C + y*s],
        [y*x*C + z*s, c + y*y*C,     y*z*C - x*s],
        [z*x*C - y*s, z*y*C + x*s, c + z*z*C]
    ])

def align_planes_and_a(a, b, aprime, bprime):
    a, b = np.array(a,float), np.array(b,float)
    aprime, bprime = np.array(aprime,float), np.array(bprime,float)
    
    # --- Step 1: 平面の法線を一致 ---
    n = np.cross(a,b); n /= np.linalg.norm(n)
    n2 = np.cross(aprime,bprime); n2 /= np.linalg.norm(n2)
    
    axis1 = np.cross(n, n2)
    if np.linalg.norm(axis1) < 1e-8:
        R1 = np.eye(3)
    else:
        axis1 /= np.linalg.norm(axis1)
        theta1 = np.arccos(np.clip(np.dot(n, n2), -1, 1))
        R1 = rotation_matrix(axis1, theta1)
        print(theta1)
    
    a1 = R1 @ a
    b1 = R1 @ b
    
    # --- Step 2: 平面上で a1 を a' に平行に ---
    a1n, a2n = a1/np.linalg.norm(a1), aprime/np.linalg.norm(aprime)
    axis2 = n2  # 平面の法線で回転
    theta2 = np.arccos(np.clip(np.dot(a1n, a2n), -1, 1))
    print(theta2)
    
    # 方向が逆の場合も考慮（符号チェック）
    if np.dot(np.cross(a1n, a2n), axis2) < 0:
        theta2 = -theta2

    R2 = rotation_matrix(axis2, theta2)
    
    # --- 合成回転 ---
    R = R2 @ R1
    return R, R @ a, R @ b

def exchange_vector(c,R):
    c = np.array(c,float)
    c_new = R @ c
    return c_new


# ==== 使用例 ====
a = [1,0,0]
b = [1,1,1]
aprime = [1,0,0]
bprime = [0,0,1]

c = [1,1,1]

R, a_rot, b_rot = align_planes_and_a(a, b, aprime, bprime)
print(R)
print("a_rot =", a_rot)
print("b_rot =", b_rot)

c_new= exchange_vector(c, R)
print("c_new =", c_new)

0.7853981633974484
0.0
[[ 1.          0.          0.        ]
 [ 0.          0.70710678 -0.70710678]
 [ 0.          0.70710678  0.70710678]]
a_rot = [1. 0. 0.]
b_rot = [ 1.00000000e+00 -1.11022302e-16  1.41421356e+00]
c_new = [ 1.00000000e+00 -1.11022302e-16  1.41421356e+00]


In [6]:
test = np.eye(3)
np.linalg.norm(test)

np.float64(1.7320508075688772)

In [7]:
test = np.clip(1.2,-1,1)
print(test)

1.0


In [8]:
a = [1,2,3]
b = [4,5,6]
print(a-b)

TypeError: unsupported operand type(s) for -: 'list' and 'list'

In [3]:
import numpy as np
import pandas as pd

df = pd.read_csv("../sample/basis_data/pa_ion.txt", sep="\\s+" ,names=["atom", "x", "y", "z"])
basis_coords = df[["x","y","z"]].to_numpy()

r1 = basis_coords[0]
r2 = basis_coords[6]
r3 = basis_coords[1]

# --- 3. 平行移動: C1を原点へ ---
t = -r1
coords = np.array([basis_coords[i] + t for i in range(len(basis_coords))])

# --- 4. 回転: C2をx軸上へ ---
x_vec = coords[6]
x_axis = x_vec / np.linalg.norm(x_vec)
axis = np.cross(x_axis, np.array([1, 0, 0]))
axis_norm = np.linalg.norm(axis)

if axis_norm > 1e-8:
    axis /= axis_norm
    theta = np.arccos(np.dot(x_axis, [1, 0, 0]))
    c, s = np.cos(theta), np.sin(theta)
    K = np.array([
        [0, -axis[2], axis[1]],
        [axis[2], 0, -axis[0]],
        [-axis[1], axis[0], 0]
    ])
    R = np.eye(3) + s * K + (1 - c) * (K @ K)
    coords = coords @ R.T

# --- 5. C3をxy平面上へ回転 ---
r3_new = coords[1]
angle_z = np.arctan2(r3_new[2], r3_new[1])
c, s = np.cos(-angle_z), np.sin(-angle_z)
R2 = np.array([
    [1, 0, 0],
    [0, c, -s],
    [0, s,  c]
])
coords = coords @ R2.T

# --- 7. 結果を確認 ---
for i in coords:
    print(i[0].round(8), i[1].round(8), i[2].round(8))

0.0 0.0 0.0
-0.75166781 1.17930378 -0.0
-2.13787476 1.08575553 0.06183375
-2.76849646 -0.15046891 0.10587404
-2.01538272 -1.31599928 0.09218
-0.63119156 -1.2391859 0.03827823
1.48874234 -0.0 0.0
-0.10816348 2.54156751 -0.16832637
0.86446617 2.61323043 -0.96061058
-0.61236772 3.50123468 0.46567239
2.16838949 -0.64853996 -0.76684524
2.01559778 0.72529313 0.99045468
-2.72596786 1.99480835 0.05720537
-3.84993728 -0.20214141 0.14488728
-2.50141004 -2.28324649 0.12642074
-0.03256725 -2.14199966 0.04239728
2.98479144 0.69255451 0.93024864


In [ ]:
# 5つめの続き

import numpy as np
import basis


conf = mol.GetConformer()
coordinates = []
for atom in mol.GetAtoms():
    pos = conf.GetAtomPosition(atom.GetIdx())
    coordinates.append([pos.x, pos.y, pos.z])

coordinates = np.array(coordinates)

c_cooh1 = cooh_list[0][0]
c_benzene1 = cooh_list[0][1]
c_cooh2 = cooh_list[1][0]
c_benzene2 = cooh_list[1][1]

aprime = [coordinates[c_benzene1] - coordinates[c_cooh1], coordinates[c_benzene2] - coordinates[c_cooh2]]
bprime = [coordinates[c_benzene2] - coordinates[c_benzene1], coordinates[c_benzene1] - coordinates[c_benzene2]]

R = basis.align_plane(aprime, bprime, ab="ab")

change = basis.change_coordinates(R, coords="ab")
print(change)

NameError: name 'mol' is not defined

In [ ]:
co_double1_index = cooh_list[0][2]
co_single1_index = cooh_list[0][3]
ch1_index = cooh_list[0][4]
co_double2_index = cooh_list[1][2]
co_single2_index = cooh_list[1][3]
ch2_index = cooh_list[1][4]
base1 = coordinates[cooh_list[0][0]]
base2 = coordinates[cooh_list[1][0]]
print(co_double1_index, co_single1_index, ch1_index)
print(co_double2_index, co_single2_index, ch2_index)
print(base1, cooh_list[0][0])
print(base2, cooh_list[1][0])

conf.SetAtomPosition(co_double1_index, base1+change[0][0])
conf.SetAtomPosition(co_single1_index, base1+change[0][1])
conf.SetAtomPosition(ch1_index, base1+change[0][2])
conf.SetAtomPosition(co_double2_index, base2+change[1][0])
conf.SetAtomPosition(co_single2_index, base2+change[1][1])
conf.SetAtomPosition(ch2_index, base2+change[1][2])
for atom in mol.GetAtoms():
    pos = conf.GetAtomPosition(atom.GetIdx())
    print(f"{atom.GetSymbol()} {pos.x:.4f} {pos.y:.4f} {pos.z:.4f}")

In [13]:
import numpy as np

a = np.array([[1,2,3],[4,5,6],[7,8,9]])
b = np.array([1,2,3])

print(a+b)

[[ 2  4  6]
 [ 5  7  9]
 [ 8 10 12]]


In [1]:
a = (1,2,3,4)
for i in a:
    print(i)

1
2
3
4


In [3]:
import numpy as np

a = np.array([1,2,3])
b = np.array([4,5,6])
c = a + b
c[0] = 10
print(a)
print(b)
print(c)

[1 2 3]
[4 5 6]
[10  7  9]


In [15]:
import pandas as pd
from rdkit import Chem
import warnings
warnings.filterwarnings("ignore", category=UserWarning, module="openpyxl")

paths = ["1-100", "101-200", "201-300", "301-400", "401-500", "501-600", "601-700", "701-800", "801-900", "901-1000"]

df = pd.read_excel(f"sample/Substance_1-100.xlsx", header=4)
df = df.dropna(subset=[df.columns[2]]).reset_index(drop=True)
x = df[df.columns[2]]
x_iso = df[df.columns[3]]
cas = df[df.columns[0]]

mol = Chem.MolFromSmiles(x[1])

print(x[1])
print(mol)
print(x_iso)
print(cas)

O=C(O)C=1C=CC=CC1C(=O)O
0     NaN
1     NaN
2     NaN
3     NaN
4     NaN
     ... 
93    NaN
94    NaN
95    NaN
96    NaN
97    NaN
Name: Isomeric SMILES, Length: 98, dtype: object
0         877-24-7
1          88-99-3
2         603-11-2
3         610-35-5
4         610-27-5
          ...     
93    1092449-37-0
94     937647-86-4
95      13810-83-8
96     499793-28-1
97      90348-28-0
Name: CAS Registry Number, Length: 98, dtype: object


In [1]:
import phthalicacid as pa
a = pa.select_smiles(x[1])
print(a)
b = pa.detect_phthalic_acid(x[1])
print(b)

NameError: name 'x' is not defined

In [3]:
pa.generate_coord(x[1],b)

O 2.1523 -0.8218 -0.6072
C 1.4917 -0.0000 -0.0000
O 2.0163 0.9413 0.7628
C 0.0000 0.0000 0.0000
C -0.6565 -1.2425 0.0676
C -2.0456 -1.3114 0.1777
C -2.8013 -0.1424 0.2231
C -2.1736 1.1004 0.1347
C -0.7622 1.1743 0.0000
C -0.1731 2.5247 -0.2045
O -0.4726 3.5008 0.4533
O 0.6721 2.5831 -1.2290
H 3.0196 0.9301 0.7161
H -0.0900 -2.1660 0.0675
H -2.5360 -2.2742 0.2411
H -3.8784 -0.1989 0.3142
H -2.7876 1.9929 0.1394
H 1.0284 3.4848 -1.3036
O 4.6432 1.0130 0.7389
H 4.9702 1.8236 0.3283
H 5.0153 0.2937 0.2125
O -2.0174 3.4108 2.8671
H -1.5112 3.9468 3.4872
H -1.5005 3.4249 2.0421

O 2.1007 -0.9290 -0.5971
C 1.5128 0.0000 0.0000
O 2.0723 0.9360 0.6352
C 0.0000 0.0000 0.0000
C -0.6638 -1.2391 -0.0726
C -2.0531 -1.2991 -0.1861
C -2.8014 -0.1253 -0.2306
C -2.1660 1.1135 -0.1380
C -0.7377 1.1875 0.0000
C -0.1388 2.5340 0.2103
O -0.5352 3.3302 1.0395
O 0.8245 2.8313 -0.6579
H -0.1024 -2.1657 -0.0737
H -2.5492 -2.2588 -0.2530
H -3.8786 -0.1748 -0.3242
H -2.7744 2.0098 -0.1421
H 1.1737 3.7171 -0.4615


In [14]:
import pandas as pd
from rdkit import Chem
import warnings
warnings.filterwarnings("ignore", category=UserWarning, module="openpyxl")

paths = ["101-200", "201-300", "301-400", "401-500", "501-600", "601-700", "701-800", "801-900", "901-1000"]

df = pd.read_excel("sample/Substance_1-100.xlsx", header=4)
for path in paths:
    df1 = pd.read_excel(f"sample/Substance_{path}.xlsx", header=4)
    df = pd.concat([df,df1], ignore_index=True)
print(df.index[2])
print(df[df.columns[2]])

2
0                            [K].O=C(O)C=1C=CC=CC1C(=O)O
1                                O=C(O)C=1C=CC=CC1C(=O)O
2                       O=C(O)C1=CC=CC(=C1C(=O)O)N(=O)=O
3                             O=C(O)C1=CC=C(O)C=C1C(=O)O
4                       O=C(O)C1=CC=C(C=C1C(=O)O)N(=O)=O
                             ...                        
995                    O=C(O)C=1C(OCC)=CC=C(OCC)C1C(=O)O
996                       O=C(O)C=1C=C2C(=CC1C(=O)O)COC2
997              O=C(O)C=1C=CC2=CC=3C=CC=CC3C=C2C1C(=O)O
998           O=C(O)C=1C=CC=CC1C=2C=CC=C(C(=O)O)C2C(=O)O
999    O=C(O)C=1C(O)=C(C(=O)O)C(C(=O)O)=C(C(=O)O)C1C(...
Name: Canonical SMILES, Length: 1000, dtype: object


In [18]:
def test():
    return 1,2,3
a = test()
print(type(a))

<class 'tuple'>


In [2]:
import phthalicacid as pa

smiles, iso, cas = pa.samples_data()

In [11]:
samples = []
for i in range(len(smiles)):
    a = pa.select_smiles(smiles[i],iso[i])
    if a:
        samples.append(a)


In [12]:
samples_new = []
phthals = []
for sample in samples:
    b = pa.detect_phthalic_acid(sample)
    if b:
        samples_new.append(sample)
        phthals.append(b)
print(samples_new[11])
print(phthals[11])

O=C(O)C1=CC(Cl)=C(Cl)C=C1C(=O)O
[[11, 10, 12, 13, 17], [1, 3, 0, 2, 14]]


In [13]:
x = pa.generate_coord(samples_new[11],phthals[11])
print(x[0][0])

0 1
O 2.1523 -0.8218 -0.6072
C 1.4917 -0.0000 -0.0000
O 2.0163 0.9413 0.7628
C 0.0000 0.0000 0.0000
C -0.6560 -1.2416 0.0671
C -2.0467 -1.3161 0.1773
Cl -2.8094 -2.8980 0.2759
C -2.8060 -0.1402 0.2231
Cl -4.5579 -0.1916 0.3714
C -2.1710 1.1010 0.1344
C -0.7622 1.1743 0.0000
C -0.1715 2.5241 -0.2040
O -0.4702 3.5004 0.4538
O 0.6742 2.5817 -1.2281
H 3.0196 0.9301 0.7161
H -0.0827 -2.1611 0.0660
H -2.7776 1.9989 0.1388
H 1.0315 3.4830 -1.3025
O 4.6432 1.0130 0.7389
H 4.9702 1.8236 0.3283
H 5.0153 0.2937 0.2125
O -2.0174 3.4108 2.8671
H -1.5112 3.9468 3.4872
H -1.5005 3.4249 2.0421



In [5]:
print(x)

(['0 1\nO 2.1523 -0.8218 -0.6072\nC 1.4917 -0.0000 -0.0000\nO 2.0163 0.9413 0.7628\nC 0.0000 0.0000 0.0000\nC -0.6638 -1.2391 -0.0726\nC -2.0531 -1.2991 -0.1861\nC -2.8014 -0.1253 -0.2306\nC -2.1660 1.1135 -0.1380\nC -0.7622 1.1743 0.0000\nC -0.1637 2.5197 0.2101\nO -0.6505 3.3733 0.9240\nO 0.9302 2.7308 -0.5152\nH 3.0196 0.9301 0.7161\nH -0.1024 -2.1657 -0.0737\nH -2.5492 -2.2588 -0.2530\nH -3.8786 -0.1748 -0.3242\nH -2.7744 2.0098 -0.1421\nH 1.2771 3.6194 -0.3266\nO 4.6432 1.0130 0.7389\nH 4.9702 1.8236 0.3283\nH 5.0153 0.2937 0.2125\nO -2.0174 3.4108 2.8671\nH -1.5112 3.9468 3.4872\nH -1.5005 3.4249 2.0421\n', '0 1\nO 2.1007 -0.9290 -0.5971\nC 1.5128 0.0000 0.0000\nO 2.0723 0.9360 0.6352\nC 0.0000 0.0000 0.0000\nC -0.6578 -1.2417 -0.0696\nC -2.0470 -1.3088 -0.1810\nC -2.8014 -0.1388 -0.2255\nC -2.1721 1.1031 -0.1351\nC -0.7377 1.1875 0.0000\nC -0.1388 2.5339 0.2109\nO -0.5349 3.3296 1.0408\nO 0.8241 2.8318 -0.6575\nH -0.0924 -2.1658 -0.0703\nH -2.5384 -2.2710 -0.2458\nH -3.8785 -0.1

In [4]:
coords = []
x = 0
for i in range(len(phthals)):
    print(x)
    x += 1
    c = pa.generate_coord(samples_new[i],phthals[i])

0
18 0
O 2.1523 -0.8218 -0.6072
C 1.4917 -0.0000 -0.0000
O 2.0163 0.9413 0.7628
C 0.0000 0.0000 0.0000
C -0.6638 -1.2391 -0.0726
C -2.0531 -1.2991 -0.1861
C -2.8014 -0.1253 -0.2306
C -2.1660 1.1135 -0.1380
C -0.7622 1.1743 0.0000
C -0.1637 2.5197 0.2101
O -0.6505 3.3733 0.9240
O 0.9302 2.7308 -0.5152
H 3.0196 0.9301 0.7161
H -0.1024 -2.1657 -0.0737
H -2.5492 -2.2588 -0.2530
H -3.8786 -0.1748 -0.3242
H -2.7744 2.0098 -0.1421
H 1.2771 3.6194 -0.3266
O 4.6432 1.0130 0.7389
H 4.9702 1.8236 0.3283
H 5.0153 0.2937 0.2125
O -2.0174 3.4108 2.8671
H -1.5112 3.9468 3.4872
H -1.5005 3.4249 2.0421

17 1
O 2.1007 -0.9290 -0.5971
C 1.5128 0.0000 0.0000
O 2.0723 0.9360 0.6352
C 0.0000 0.0000 0.0000
C -0.6578 -1.2417 -0.0696
C -2.0470 -1.3088 -0.1810
C -2.8014 -0.1388 -0.2255
C -2.1721 1.1031 -0.1351
C -0.7377 1.1875 0.0000
C -0.1388 2.5339 0.2109
O -0.5349 3.3296 1.0408
O 0.8241 2.8318 -0.6575
H -0.0924 -2.1658 -0.0703
H -2.5384 -2.2710 -0.2458
H -3.8785 -0.1939 -0.3172
H -2.7844 1.9968 -0.1387
H 1.1

In [2]:
freeze_atoms = [7, 11, 13, 9, 12, 14]  # <- ←→ 実際のインデックスに置き換えてください

# constraints ブロックを自動生成
constraints_text = "\nconstraints {\n"
for idx in freeze_atoms:
    constraints_text += f"  fix atom {idx}\n"
constraints_text += "}\n"

In [3]:
print(constraints_text)
print(type(constraints_text))


constraints {
  fix atom 7
  fix atom 11
  fix atom 13
  fix atom 9
  fix atom 12
  fix atom 14
}

<class 'str'>


In [4]:
test = []
for i in range(2):
    test.append(constraints_text)
print(test)

['\nconstraints {\n  fix atom 7\n  fix atom 11\n  fix atom 13\n  fix atom 9\n  fix atom 12\n  fix atom 14\n}\n', '\nconstraints {\n  fix atom 7\n  fix atom 11\n  fix atom 13\n  fix atom 9\n  fix atom 12\n  fix atom 14\n}\n']


In [24]:
print(test[0])


constraints {
  fix atom 7
  fix atom 11
  fix atom 13
  fix atom 9
  fix atom 12
  fix atom 14
}



In [7]:
a = [[1,3],[4,5]]
y = [x for row in a for x in row]
print(a)
print(y)
y[3] = 12
print(a)
print(y)

[[1, 3], [4, 5]]
[1, 3, 4, 5]
[[1, 3], [4, 5]]
[1, 3, 4, 12]


In [8]:
a = [1,2,3]
b = []
b.append(a)
a = [1,2]
b.append(a)
print(b)

[[1, 2, 3], [1, 2]]


In [1]:
for i in range(1,10,2):
    print(i)

1
3
5
7
9


In [3]:
import pandas as pd
a = [[1,2,3],[4,5,6]]
df = pd.DataFrame(a, columns=["A","B","C"])
print(df)

   A  B  C
0  1  2  3
1  4  5  6
